In [1]:
import os
import torch

os.environ["CUDA_VISIBLE_DEVICES"] = "6"
n_gpu = torch.cuda.device_count()

/home/m13519061/anaconda3/envs/absa/lib/python3.9/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
tasks = {
    "single" : ['a', 'o'],
    "simple" : ["oa", "as"],
    "complex" : ["oas"]
}

In [3]:
combination_tasks = [
    # tasks["simple"],
    tasks["complex"],
    tasks["single"] + tasks["simple"],
    tasks["single"] + tasks["complex"],
    tasks["simple"] + tasks["complex"],
    tasks["single"] + tasks["simple"] + tasks["complex"]
]

In [4]:
combination_tasks

[['oas'],
 ['a', 'o', 'oa', 'as'],
 ['a', 'o', 'oas'],
 ['oa', 'as', 'oas'],
 ['a', 'o', 'oa', 'as', 'oas']]

In [5]:
all_task = combination_tasks[-1]
print(all_task)

['a', 'o', 'oa', 'as', 'oas']


In [6]:
import sys
sys.path.append("../../../src/")
import data_utils

directory = dict(
    lap14 = "../../../data/absa/en/peng/14lap",
    res14 = "../../../data/absa/en/peng/14res",
    res15 = "../../../data/absa/en/peng/15res",
    res16 = "../../../data/absa/en/peng/16res"
)

In [7]:
data = dict(
    lap14 = dict(
        train = data_utils.read_data(path=directory["lap14"] + "/train_triplets.txt",
                                     target_format="aos"),
        val = data_utils.read_data(path=directory["lap14"] + "/dev_triplets.txt",
                                     target_format="aos"),
        test = data_utils.read_data(path=directory["lap14"] + "/test_triplets.txt",
                                     target_format="aos")
    ),
    res14 = dict(
        train = data_utils.read_data(path=directory["res14"] + "/train_triplets.txt",
                                     target_format="aos"),
        val = data_utils.read_data(path=directory["res14"] + "/dev_triplets.txt",
                                     target_format="aos"),
        test = data_utils.read_data(path=directory["res14"] + "/test_triplets.txt",
                                     target_format="aos")
    ),
    res15 = dict(
        train = data_utils.read_data(path=directory["res15"] + "/train_triplets.txt",
                                     target_format="aos"),
        val = data_utils.read_data(path=directory["res15"] + "/dev_triplets.txt",
                                     target_format="aos"),
        test = data_utils.read_data(path=directory["res15"] + "/test_triplets.txt",
                                     target_format="aos")
    ),
    res16 = dict(
        train = data_utils.read_data(path=directory["res16"] + "/train_triplets.txt",
                                     target_format="aos"),
        val = data_utils.read_data(path=directory["res16"] + "/dev_triplets.txt",
                                     target_format="aos"),
        test = data_utils.read_data(path=directory["res16"] + "/test_triplets.txt",
                                     target_format="aos")
    )
)

In [8]:
from copy import deepcopy

data_intermediate = dict()

for domain, v1 in data.items():
    data_intermediate[domain] = dict()
    for task in all_task:
        data_intermediate[domain][task] = dict()
        for split in v1.keys():
            ds = data[domain][split]
            ds_copy = deepcopy(ds)
            for i in range(len(ds_copy)):
                # Reduce
                ds_copy[i]["target"] = data_utils.reduce_targets(ds_copy[i]["target"],task)
                # Remove Duplicates
                ds_copy[i]["target"] = data_utils.remove_duplicate_targets(ds_copy[i]["target"])
            data_intermediate[domain][task][split] = ds_copy

In [9]:
data_intermediate

{'lap14': {'a': {'train': [{'text': 'I charge it at night and skip taking the cord with me because of the good battery life .',
     'target': [{'aspect': 'battery life'}]},
    {'text': 'it is of high quality , has a killer GUI , is extremely stable , is highly expandable , is bundled with lots of very good applications , is easy to use , and is absolutely gorgeous .',
     'target': [{'aspect': 'quality'},
      {'aspect': 'GUI'},
      {'aspect': 'applications'},
      {'aspect': 'use'}]},
    {'text': 'Easy to start up and does not overheat as much as other laptops .',
     'target': [{'aspect': 'start up'}]},
    {'text': 'Great laptop that offers many great features !',
     'target': [{'aspect': 'features'}]},
    {'text': 'One night I turned the freaking thing off after using it , the next day I turn it on , no GUI , screen all dark , power light steady , hard drive light steady and not flashing as it usually does .',
     'target': [{'aspect': 'GUI'},
      {'aspect': 'screen'

In [10]:
mask = "<extra_id_X>"

In [11]:
# def construct_answer(targets,se_order):
#     result = []
#     for t in targets:
#         constructed_t = []
#         for se in se_order:
#             element = t[data_utils.SENTIMENT_ELEMENT[se]]
#             for k, v in added_tokens.items():
#                 element = element.replace(k,v)
#             constructed_t.append(element)
#         constructed_t = " , ".join(constructed_t)
#         constructed_t = f"( {constructed_t} )"
#         result.append(constructed_t)
#     result = " ; ".join(result)
#     return result

def construct_answer(targets,se_order):
    result = []
    counter = 0
    for t in targets:
        constructed_t = ""
        for se in se_order:
            counter = counter % 100
            constructed_t += ' ' + mask.replace('X',str(counter)) + ' ' + t[data_utils.SENTIMENT_ELEMENT[se]]
            counter += 1
        constructed_t = constructed_t.strip()
        result.append(constructed_t)
    result = " ; ".join(result)
    return result

In [12]:
data_intermediate["lap14"]["oas"]["train"][1]

{'text': 'it is of high quality , has a killer GUI , is extremely stable , is highly expandable , is bundled with lots of very good applications , is easy to use , and is absolutely gorgeous .',
 'target': [{'aspect': 'quality', 'opinion': 'high', 'sentiment': 'positive'},
  {'aspect': 'GUI', 'opinion': 'killer', 'sentiment': 'positive'},
  {'aspect': 'applications', 'opinion': 'good', 'sentiment': 'positive'},
  {'aspect': 'use', 'opinion': 'easy', 'sentiment': 'positive'}]}

In [13]:
ans = construct_answer(data_intermediate["lap14"]["oas"]["train"][1]["target"],"oas")
ans

'<extra_id_0> high <extra_id_1> quality <extra_id_2> positive ; <extra_id_3> killer <extra_id_4> GUI <extra_id_5> positive ; <extra_id_6> good <extra_id_7> applications <extra_id_8> positive ; <extra_id_9> easy <extra_id_10> use <extra_id_11> positive'

In [14]:
# def construct_prompt(text,se_order):
#     prompt = []
#     for se in se_order:
#         prompt.append(data_utils.SENTIMENT_ELEMENT[se])
#     prompt = " , ".join(prompt)
#     prompt = f"( {prompt} )"
#     masked_text = text
#     for k, v in added_tokens.items():
#         masked_text = masked_text.replace(k,v)
#     result = masked_text + " | " + prompt
#     return result

def construct_prompt(text,se_order):
    prompt = []
    for counter, se in enumerate(se_order):
        prompt.append(data_utils.SENTIMENT_ELEMENT[se] + " : " + mask.replace('X',str(counter)))
    prompt = " ,".join(prompt)
    result = text + "| " + prompt
    return result

In [15]:
pro = construct_prompt(data_intermediate["lap14"]["oas"]["train"][1]["text"],"oas")
pro

'it is of high quality , has a killer GUI , is extremely stable , is highly expandable , is bundled with lots of very good applications , is easy to use , and is absolutely gorgeous .| opinion : <extra_id_0> ,aspect : <extra_id_1> ,sentiment : <extra_id_2>'

In [16]:
import re

# def catch_answer(output,se_order):
#     output = output.replace("<pad>",'')
#     output = output.replace("</s>",'')
#     pattern = []
#     for se in se_order:
#         if se != 's':
#             pattern.append(f"\s*(?P<{data_utils.SENTIMENT_ELEMENT[se]}>[^;]+)\s*")
#         else:
#             pattern.append(f"\s*(?P<{data_utils.SENTIMENT_ELEMENT['s']}>positive|negative|neutral)\s*")
#     pattern = ','.join(pattern)
#     pattern = f"\({pattern}\)"
#     found = [found_iter.groupdict() for found_iter in re.finditer(pattern,output)]
#     for i in range(len(found)):
#         for k, v in found[i].items():
#             found[i][k] = found[i][k].strip()
#     return found

def catch_answer(output,se_order):
    output = output.replace("<pad>",'')
    output = output.replace("</s>",'')
    pattern = r""
    for se in se_order:
        if se != 's':
            pattern += f"<extra_id_\d+>\s*(?P<{data_utils.SENTIMENT_ELEMENT[se]}>[^;]+)\s*"
        else:
            pattern += f"<extra_id_\d+>\s*(?P<{data_utils.SENTIMENT_ELEMENT['s']}>positive|negative|neutral)\s*"
    found = [found_iter.groupdict() for found_iter in re.finditer(pattern,output)]
    for i in range(len(found)):
        for k, v in found[i].items():
            found[i][k] = found[i][k].strip()
    return found

In [17]:
catched_ans = catch_answer(ans,"oas")
print(catched_ans)
print(catched_ans == data_intermediate["lap14"]["oas"]["train"][1]["target"])

[{'opinion': 'high', 'aspect': 'quality', 'sentiment': 'positive'}, {'opinion': 'killer', 'aspect': 'GUI', 'sentiment': 'positive'}, {'opinion': 'good', 'aspect': 'applications', 'sentiment': 'positive'}, {'opinion': 'easy', 'aspect': 'use', 'sentiment': 'positive'}]
True


In [18]:
from transformers import AutoTokenizer

tokenizer = AutoTokenizer.from_pretrained("t5-base")

/home/m13519061/anaconda3/envs/absa/lib/python3.9/site-packages/transformers/models/t5/tokenization_t5_fast.py:156: FutureWarning: This tokenizer was incorrectly instantiated with a model max length of 512 which will be corrected in Transformers v5.
For now, this behavior is kept to avoid breaking backwards compatibility when padding/encoding with `truncation is True`.
- Be aware that you SHOULD NOT rely on t5-base automatically truncating your input to 512 when padding/encoding.
- If you want to encode/pad to sequences longer than 512 you can either instantiate this tokenizer with `model_max_length` or pass `max_length` when encoding/padding.
- To avoid this warning, please instantiate this tokenizer with `model_max_length` set to your preferred value.
  warnings.warn(


In [19]:
encoding_args = {
    "max_length" : 128,
    "padding" : True,
    "truncation" : True,
    "return_tensors" : "pt"
}

In [20]:
def encode(dataset):
    result = tokenizer(dataset["input"], text_target=dataset["output"], **encoding_args)
    return result

In [21]:
from datasets import Dataset

def create_data_2(tasks):
    data_2 = {
        "train" : [],
        "val" : [],
        "test" : []
    }
    for domain, v1 in data_intermediate.items():
        # data_2[domain] = {
        #     "train" : [], # basic task
        #     "val" : [], # complex task
        #     "test" : [] # complex task
        # }
        # TRAIN
        for basic_task in tasks:
            for el in data_intermediate[domain][basic_task]["train"]:
                data_2["train"].append({
                        "input" : construct_prompt(el["text"],basic_task),
                        "output" : construct_answer(el["target"],basic_task),
                        "task" : basic_task
                    })
        # VAL
        for el in data_intermediate[domain]["oas"]["val"]:
            data_2["val"].append({
                    "input" : construct_prompt(el["text"],"oas"),
                    "output" : construct_answer(el["target"],"oas"),
                    "task" : "oas"
                })
        # TEST
        for el in data_intermediate[domain]["oas"]["test"]:
            data_2["test"].append({
                    "input" : construct_prompt(el["text"],"oas"),
                    "output" : construct_answer(el["target"],"oas"),
                    "task" : "oas"
                })
    data_2["train"] = Dataset.from_list(data_2["train"])
    data_2["val"] = Dataset.from_list(data_2["val"])
    data_2["test"] = Dataset.from_list(data_2["test"])
    
    data_tok = dict()
    # for domain, v1 in data_2.items():
    for split, v1 in data_2.items():
        if split != "test":
            data_tok[split] = data_2[split].map(encode,batched=True,remove_columns=["input","output","task"])
        else:
            data_tok[split] = encode(data_2[split])
    
    return data_2, data_tok

In [22]:
data_2, data_tok = create_data_2(combination_tasks[0])

In [23]:
data_2

{'train': Dataset({
     features: ['input', 'output', 'task'],
     num_rows: 3634
 }),
 'val': Dataset({
     features: ['input', 'output', 'task'],
     num_rows: 887
 }),
 'test': Dataset({
     features: ['input', 'output', 'task'],
     num_rows: 1468
 })}

In [24]:
data_2["train"][0]

{'input': 'I charge it at night and skip taking the cord with me because of the good battery life .| opinion : <extra_id_0> ,aspect : <extra_id_1> ,sentiment : <extra_id_2>',
 'output': '<extra_id_0> good <extra_id_1> battery life <extra_id_2> positive',
 'task': 'oas'}

In [25]:
data_2["val"][0]

{'input': 'In the shop , these MacBooks are encased in a soft rubber enclosure - so you will never know about the razor edge until you buy it , get it home , break the seal and use it ( very clever con ) .| opinion : <extra_id_0> ,aspect : <extra_id_1> ,sentiment : <extra_id_2>',
 'output': '<extra_id_0> soft <extra_id_1> rubber enclosure <extra_id_2> positive',
 'task': 'oas'}

In [26]:
data_2["test"][0]

{'input': 'Boot time is super fast , around anywhere from 35 seconds to 1 minute .| opinion : <extra_id_0> ,aspect : <extra_id_1> ,sentiment : <extra_id_2>',
 'output': '<extra_id_0> fast <extra_id_1> Boot time <extra_id_2> positive',
 'task': 'oas'}

In [27]:
from transformers import DataCollatorForSeq2Seq

data_collator = DataCollatorForSeq2Seq(tokenizer=tokenizer)

In [28]:
from transformers import EvalPrediction
from evaluation import recall, precision, f1_score, summary_score
from typing import List, Dict, Tuple
import numpy as np

def seperate_target_prediction_per_task(predictions:List[List[Dict]],targets:List[List[Dict]],tasks:List) -> Tuple[Dict[str,List],Dict[str,List]]:
    per_task_targets = {}
    per_task_predictions = {}
    for target, prediction, task in zip(targets,predictions,tasks):
        if task not in per_task_targets.keys():
            per_task_targets[task] = []
        if task not in per_task_predictions.keys():
            per_task_predictions[task] = []
        per_task_targets[task].append(target)
        per_task_predictions[task].append(prediction)
    return per_task_targets, per_task_predictions

def preprocess_eval_preds(eval_preds:EvalPrediction,decoding_args:Dict[str,str],tokenizer:AutoTokenizer):
    input_ids = eval_preds.inputs
    target_ids = eval_preds.label_ids
    pred_ids = eval_preds.predictions

    # In case the model returns more than the prediction logits
    if isinstance(input_ids, tuple):
        input_ids = input_ids[0]
    if isinstance(target_ids, tuple):
        target_ids = target_ids[0]
    if isinstance(pred_ids, tuple):
        pred_ids = pred_ids[0]
    
    input_ids = np.argmax(input_ids,axis=-1) if len(input_ids.shape) == 3 else input_ids # in case not predict with generate
    target_ids = np.argmax(target_ids,axis=-1) if len(target_ids.shape) == 3 else target_ids # in case not predict with generate
    prediction_ids = np.argmax(pred_ids,axis=-1) if len(pred_ids.shape) == 3 else pred_ids # in case not predict with generate

    input_ids = [[token for token in row if token != -100] for row in input_ids]
    target_ids = [[token for token in row if token != -100] for row in target_ids]
    prediction_ids = [[token for token in row if token != -100] for row in prediction_ids]

    inputs = tokenizer.batch_decode(input_ids,**decoding_args)
    targets = tokenizer.batch_decode(target_ids,**decoding_args)
    predictions = tokenizer.batch_decode(prediction_ids,**decoding_args)

    return inputs, targets, predictions

def compute_metrics(eval_preds:EvalPrediction,decoding_args:Dict[str,str],tokenizer:AutoTokenizer,tasks:List) -> Dict[str,float]: # MAY NOT BE SUFFICIATE FOR CAUSAL LM
        """
        ### DESC
            Method to compute the metrics.
        ### PARAMS
        * eval_preds: EvalPrediction instance from training.
        * decoding_args: Decoding arguments.
        ### RETURN
        * metrics: Dictionary of metrics.
        """
        inputs, targets, predictions = preprocess_eval_preds(eval_preds,decoding_args,tokenizer)

        targets = [catch_answer(text,task) for text,task in zip(targets,tasks) if task != "non_absa"]
        predictions = [catch_answer(text,task) for text,task in zip(predictions,tasks) if task != "non_absa"]


        per_task_targets, per_task_predictions = seperate_target_prediction_per_task(predictions, targets, tasks)
        
        metrics = {}

        metrics["overall_recall"] = recall(predictions,targets)
        metrics["overall_precision"] = precision(predictions,targets)
        metrics["overall_f1_score"] = f1_score(predictions,targets)

        for task in per_task_targets.keys():
            if task == "non_absa":
                continue
            metrics[f"{task}_recall"] = recall(per_task_predictions[task],per_task_targets[task])
            metrics[f"{task}_precision"] = precision(per_task_predictions[task],per_task_targets[task])
            metrics[f"{task}_f1_score"] = f1_score(per_task_predictions[task],per_task_targets[task])
        
        return metrics

In [29]:
from transformers import Seq2SeqTrainingArguments

train_args = {
    "num_train_epochs": 10,
    "learning_rate": 3e-4,
    "save_total_limit": 2,
    "gradient_accumulation_steps": 2,
    "per_device_train_batch_size": 16//n_gpu,
    "per_device_eval_batch_size": 16//n_gpu,
    "save_strategy": "epoch",
    "evaluation_strategy": "epoch",
    "logging_strategy" : "epoch",
    "metric_for_best_model": "overall_f1_score",
    "load_best_model_at_end": True,
    "adam_epsilon": 1e-08,
    "output_dir": "./output",
    "logging_dir" : "./output/log",
    "include_inputs_for_metrics" : True
}

train_args = Seq2SeqTrainingArguments(**train_args)

In [30]:
import torch
device = torch.device("cuda:0") if torch.cuda.is_available() else torch.device("cpu")
print(device)

cuda:0


In [31]:
from transformers import Seq2SeqTrainer

decoding_args = {
    "skip_special_tokens" : False
}

def preprocess_logits_for_metrics(logits, targets):
    pred_logits = logits[0] if isinstance(logits,tuple) else logits
    pred_ids = torch.argmax(pred_logits, dim=-1)
    return pred_ids, targets

In [32]:
from tqdm import tqdm
from typing import List, Dict

def generate_predictions(model,tokenizer,data,device=torch.device("cuda:0"),decoding_args:Dict={}) -> List[str]:
    # Data loader
    # input_ids_data_loader = torch.utils.data.DataLoader(tokenized["input_ids"],
    #                     batch_size=batch_size,shuffle=False)
    # attention_mask_data_loader = torch.utils.data.DataLoader(tokenized["attention_mask"],
    #                     batch_size=batch_size,shuffle=False)
    # Predict
    model = model
    tokenizer = tokenizer
    tensor_predictions = []
    with torch.no_grad():
        for text in tqdm(data):
            # input_ids = input_ids.to(device)
            # attention_mask = attention_mask.to(device)
            input_ids = tokenizer(text, return_tensors="pt").input_ids.to(device)
            tensor_predictions.extend(model.generate(input_ids=input_ids, pad_token_id=tokenizer.pad_token_id,eos_token_id=tokenizer.eos_token_id,max_length=128).cpu())
            input_ids = input_ids.cpu()
            # attention_mask = attention_mask.cpu()
    tensor_predictions = [[token for token in row if token != -100] for row in tensor_predictions]
    predictions = tokenizer.batch_decode(tensor_predictions,**decoding_args)
    predictions = [el for el in predictions]
    return predictions

In [33]:
import json

def save_result(str_preds_,preds,targets,filename):
    result = []
    str_preds = [el.replace("<pad>",'').replace("</s>",'') for el in str_preds_]
    assert len(str_preds) == len(preds) == len(targets)
    for i in range(len(str_preds)):
        result.append({
            "str_pred" : str_preds[i],
            "pred" : preds[i],
            "target" : targets[i]
        })
    
    with open(filename,'w') as fp:
        json.dump(result,fp)
    return result

In [34]:
from transformers import AutoModelForSeq2SeqLM
import torch

for combo_task in combination_tasks:
    data_2, data_tok = create_data_2(combo_task)
    model = AutoModelForSeq2SeqLM.from_pretrained("t5-base")
    model.to(device)
    trainer = Seq2SeqTrainer(
            model = model,
            args = train_args,
            tokenizer = tokenizer,
            data_collator = data_collator,
            train_dataset = data_tok["train"],
            eval_dataset = data_tok["val"],
            compute_metrics = lambda eval_preds: compute_metrics(eval_preds,decoding_args,tokenizer,data_2["val"]["task"]),
            preprocess_logits_for_metrics = preprocess_logits_for_metrics
        )

    trainer.train()

    str_preds = generate_predictions(model, tokenizer, data_2["test"]["input"], device, decoding_args)
    preds = [catch_answer(el,"oas") for el in str_preds]
    targets = [catch_answer(el,"oas") for el in data_2["test"]["output"]]
    score = summary_score(preds,targets)

    del model
    torch.cuda.empty_cache()

    fname = '-'.join(combo_task) + ".json"

    result = save_result(str_preds, preds, targets, fname)

/home/m13519061/anaconda3/envs/absa/lib/python3.9/site-packages/transformers/optimization.py:306: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(
***** Running training *****
  Num examples = 3634
  Num Epochs = 10
  Instantaneous batch size per device = 16
  Total train batch size (w. parallel, distributed & accumulation) = 32
  Gradient Accumulation steps = 2
  Total optimization steps = 1140
  Number of trainable parameters = 222903552
You're using a T5TokenizerFast tokenizer. Please note that with a fast tokenizer, using the `__call__` method is faster than using a method to encode the text followed by a call to the `pad` method to get a padded encoding.


***** Running Evaluation *****
  Num examples = 887
  Batch size = 16
  Num examples = 887
  Batch size = 16
Saving model checkpoint to ./output/checkpoint-341
Configuration saved in ./output/checkpoint-341/config.json
Model weights saved in ./output/checkpoint-341/pytorch_model.bin
tokenizer config file saved in ./output/checkpoint-341/tokenizer_config.json
Special tokens file saved in ./output/checkpoint-341/special_tokens_map.json
Copy vocab file to ./output/checkpoint-341/spiece.model
Deleting older checkpoint [output/checkpoint-3069] due to args.save_total_limit
***** Running Evaluation *****
  Num examples = 887
  Batch size = 16
Saving model checkpoint to ./output/checkpoint-682
Configuration saved in ./output/checkpoint-682/config.json
Model weights saved in ./output/checkpoint-682/pytorch_model.bin
tokenizer config file saved in ./output/checkpoint-682/tokenizer_config.json
Special tokens file saved in ./output/checkpoint-682/special_tokens_map.json
Copy vocab file to ./output

In [35]:
import os

results_fname = [el for el in os.listdir() if el.endswith(".json")]
results = {
    fname[:-5] : json.load(open(fname,'r')) for fname in results_fname
}

In [36]:
all_score = {}

for task, v1 in results.items():
    preds = [el["pred"] for el in v1]
    targets = [el["target"] for el in v1]
    score = summary_score(preds, targets)
    all_score[task] = score

In [37]:
for k,v in all_score.items():
    print("TASK:",k)
    print(v)
    print("======================")

TASK: a-o-oas
{'recall': 0.7367797947908445, 'precision': 0.7293291731669267, 'f1_score': 0.7330355523156206}
TASK: a-o-oa-as
{'recall': 0.6089187056037885, 'precision': 0.7077625570776256, 'f1_score': 0.6546305052642241}
TASK: oa-as-oas
{'recall': 0.744277821625888, 'precision': 0.7215238095238096, 'f1_score': 0.7327242074118686}
TASK: oa-as
{'recall': 0.39739542225730073, 'precision': 0.6997915218902016, 'f1_score': 0.5069217216209414}
TASK: oas
{'recall': 0.7249408050513023, 'precision': 0.7379807692307693, 'f1_score': 0.7314026703325919}
TASK: a-o-oa-as-oas
{'recall': 0.7486187845303868, 'precision': 0.7332817935833011, 'f1_score': 0.740870923647725}
